# $\textbf{Part 1. Predicting LFSR States Using Feedforward Neural Networks}$
$\text{Author: Ryan Burns}$

#### $\textbf{Linear Feedback Shift Registers (LFSRs)}$
$\text{For background on LFSRs and maximum-length }m\text{-sequences, visit: }\textit{https://en.wikipedia.org/wiki/Linear-feedback_shift_register.}$
$\text{It is assumed that a finite list of primitive polynomial coefficients (stored as hex values) are available for the polynomial degree specified below}$
$\text{via a locally stored file with name <degree>.txt. For degree-10 polynomials, for example, the corresponding primitive polynomial coefficients}$
$\text{would have file name 10.txt. LFSRs are built for each polynomial, each yielding a pseudorandom binary sequence of length/period }2^{\text{degree}}-1.$

#### $\textbf{Prediction of LFSR State }n + 1\textbf{ Given State }n$
$\text{Suppose we are given an arbitrary LFSR feedback polynomial and we build a representation of the LFSR in software. Using this LFSR, and}$
$\text{assuming the feedback polynomial is primitive in a polynomial ring of fixed degree over }GF(2)\text{, we can generate a maximum-length binary}$
$\text{sequence which has well-documented correlation properties which make them desirable building blocks for stream ciphers or spread-spectrum}$
$\text{codes, to name a few examples. On their own, LFSRs do not afford any real cryptographic protection, being famously susceptible to correlation}$
$\text{attacks. Speaking of attacks, our goal in this notebook is to demonstrate that we can use a }\textit{very}\text{ simple neural network to predict LFSR behavior.}$
$\text{Specifically, we posit that a two-layer (i.e., single hidden-layer) feedforward neural network can readily predict the state-evolution of an arbitrary}$
$\text{LFSR. For simplicity, we constrain this network to have a very specific architecture. Its input layer consists of a fixed-length binary vector that}$
$\text{represents the LFSR state vector at some time index (epoch) }n\text{. We use the ground truth register state at index / epoch }n + 1\text{ to train a the network}$
$\text{to develop a latent representation of the finite field recursion. Both layers of the network are sigmoid connections, representing soft approximations}$
$\text{of boolean gates, outputing activations in the unit interval, }[0,1].\text{ These layers assume no bias terms, only weighted combinations of inputs. For}$
$\text{an LFSR of recursion-order/polynomial degree }deg\text{, the first (and only) hidden layer consists a total of }deg + 2\text{ weighted sigmoidal activations.}$
$\text{The output layer consists of the }deg\text{ total activations predicting }deg\text{ total bits in the LFSR state vector at epoch }n + 1\text{, for all }n\text{. These binary}$
$\text{activations are trained against the true LFSR state vectors at these indices }n + 1\text{ using a binary cross-entropy error function. The population of}$
$\text{observations are the }deg\text{-length LFSR states across all epochs in one full }m\text{-sequence period / cycle. The labels for the error function are the }$
$deg\text{-length state vector values upon 1 iteration of the LFSR recursion, per observation.}$

#### $\textbf{Part 1 of This Notebook}$
$\text{Part 1 of this notebook prototypes a feedforward binary (bias-less) neural network using Keras, training it as described above using RMSprop. The}$
$\text{model is given too few degrees of freedom to completely memorize the bits, so it must learn a latent representation of the underlying finite field}$
$\text{mathematics defining the recurrence relation. After sufficiently many training epochs, the model has been tested to converge to 100}\%\text{ accuracy}$
$\text{for all degree-10 primitive polynomials in the file 10.txt. Primitive polynomials defining }m\text{-sequences for other polynomial degrees are available}$
$\text{for download at the following site: }\textit{https://users.ece.cmu.edu/~koopman/lfsr/index.html}\text{. Future efforts may build this proof-of-concept out to}$
$\text{higher degree recursions and more complicated kinds of stream ciphers. For now, we demonstrate that a relatively shallow binary network is}$
$\text{sufficiently powerful to "crack" (i.e., predict) an LFSR's underlying recursive state vector mapping.}$

$\text{In addition to training the network, we animate the results in a plot which depicts the time-evolution of the LFSR recursion and the neural}$
$\text{network's state predictions. In addition, options are provided for plotting the correlation properties of the }m\text{-sequence training data and the Keras}$
$\text{model metrics vs training epoch, respectively. Documentation and source code for all the functions below can be found in this repo's modules.}$

### $\textbf{Import Dependencies}$

In [1]:
# System imports
from os import environ
from time import time

# So numpy and Tensorflow can cooperate
environ['KMP_DUPLICATE_LIB_OK']='True'

# Numpy imports
from numpy import array, matmul, transpose, identity, hstack, vstack, shape
from numpy import expand_dims, zeros, correlate, linspace, arange, max, roll

# Galois / LFSR utilities
from galois_tools import *
from m_sequence_viz import *
from lfsr_network_viz import *
from ml_utils import *

# Plotting functionality
from matplotlib import pyplot as plt
from matplotlib.animation import FuncAnimation

# Tensorflow/Keras functionality
from tensorflow.keras.layers import Input, Dense
from tensorflow.keras.models import Model;
from tensorflow.keras.optimizers import RMSprop;
from tensorflow.keras.metrics import TruePositives, FalsePositives, TrueNegatives, FalseNegatives;

### $\textbf{Plotting Macro (Requires IPython)}$

In [2]:
%matplotlib notebook

### $\textbf{Specify LFSR & Neural Net Parameters}$

In [3]:
###########################
# Specify LFSR parameters #
###########################

# Primitive polynomial degree
deg = 10 # (= number of bits)

# Length of m-sequence generated
M = 2**deg - 1 # (bits)

# Initial state of register
seed = 1 # (decimal form)

# Primitive polynomial choice
p = 16 # (index in catalog)

###############################
# Network training parameters #
###############################

# Number of RMSprop training epochs
N_epoch = 20000

# Batch size equal to m-sequence length
N_batch = 2**deg - 1

# Learning rate for RMSprop
learning_rate = 0.001

#########################
# Behavioral parameters #
#########################

# Turn ON/OFF correlation plot
plot_correlations = True

# Turn ON/OFF true vs. predicted mask plot
plot_prediction_masks = True

# Turn ON/OFF tapped vs. normal LFSR state observations
enable_tapped_register_obs = False

# Turn ON/OFF visualzation of metrics vs. training epoch
plot_metrics_versus_epoch = True

### $\textbf{Load Primitive Polynomial Coefficients of Specified Degree Over }GF(2)$

In [4]:
#############################################################
# Load coeff. of primitive polynomials over GF(2) from file #
#############################################################

# Read list of primitive polynomial coefficients for definition
# of the linear feedback shift registers yielding m-sequences
coeff_catalog = read_polynomials_from_file(deg=deg,
    path='./primitive_polynomials/')

###########################################################
# Generate linear feedback shift registers w/ polynomials #
###########################################################

# Define a bank of LFSRs - 1 per polynomial in the catalog
LFSRs = [LFSR(mask=eval(hex2bin(coeff_catalog[n], nbits=deg)), 
    seed=seed, order=deg, register_id=str(n)) 
    for n in range(len(coeff_catalog))]

### $\textbf{Visualize Auto- & Cross-Correlations of Two m-Sequences}$

In [5]:
# Optional correlation plot...
if plot_correlations:

    ##################################################
    # Generate m-sequences for each LFSR in the bank #
    ##################################################

    # Maximimum length binary sequences of length M = 2^deg - 1 via LFSRs
    m_sequences = vstack(tuple(register.m_sequence() for register in LFSRs))

    # Convert m-sequences from logical {0,1} to algebraic {-1,+1} representation
    algebraic_m_sequences = m_sequences.astype('float64') * 2 - 1

    ###################################################
    # Visualize correlation properties of m-sequences #
    ###################################################

    # Plot the correlations of the 1st 2 m-sequences generated above
    correlation_example(m_sequence0=algebraic_m_sequences[p,:], 
        m_sequence1=algebraic_m_sequences[p + 1,:],  deg=deg)

<IPython.core.display.Javascript object>

### $\textbf{Form Observations of }n^{\text{th}}\textbf{ LFSR State for Prediction of }(n + 1)^\text{st}\textbf{ State, for }n=0,1,2,\ldots$

In [6]:
#######################################################
# Observation vectors by streaming LFSR tapped at 0x1 #
#######################################################

# Tap LFSR or simply use state sequence?...
if enable_tapped_register_obs:

    # Observations formed by tapping a p'th LFSR from a list of options
    X, Y = form_tap_based_obs(LFSRs, p, deg)

#######################################################
# Observation vectors: LFSR state vs. epoch / index n #
#######################################################

# Use state sequence...
else:

    # Observations of 1 period of p'th LFSR in list
    X, Y = register_state_observations(LFSRs[p])

### $\textbf{Define Feedforward Binary Neural Network}$

In [7]:
# Use Keras to define feedforward binary neural network, with
# two sigmoidal layers (without bias terms) for estimation of
# the LFSR state vector at epoch n + 1 from the state at epoch n
model = feedforward_lfsr_predictor(deg=deg, num_hidden=(deg + 2),
    learning_rate=learning_rate, print_summary=True)

Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input (InputLayer)           [(None, 10)]              0         
_________________________________________________________________
hidden (Dense)               (None, 12)                120       
_________________________________________________________________
output (Dense)               (None, 10)                120       
Total params: 240
Trainable params: 240
Non-trainable params: 0
_________________________________________________________________


### $\textbf{Fit Sigmoid Model to Predict Register State }n + 1\textbf{ from State }n$

In [8]:
# Model training (save history)
model_history = model.fit(
    
    # Input dataset
    x=X, # state vectot "observation" bits
    y=Y, # future-state predicted bits
    
    # Batch size
    batch_size=N_batch,
    
    # Number of training epochs
    epochs=N_epoch,
    
    # Print progress
    verbose=1,
    
    # Set aside fraction for validation
    validation_split=0, # (use everything)
    
    # False for time series
    shuffle=False,
    
    # Parallelize job across 2 workers
    workers=1,
    use_multiprocessing=False);

Train on 1023 samples
Epoch 1/20000
1023/1023 [==============================] - 1s 1ms/sample - loss: 0.7318 - true_positives: 3571.0000 - true_negatives: 1545.0000 - false_positives: 3565.0000 - false_negatives: 1549.0000
Epoch 2/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.7288 - true_positives: 3558.0000 - true_negatives: 1559.0000 - false_positives: 3551.0000 - false_negatives: 1562.0000
Epoch 3/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.7267 - true_positives: 3548.0000 - true_negatives: 1570.0000 - false_positives: 3540.0000 - false_negatives: 1572.0000
Epoch 4/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.7251 - true_positives: 3541.0000 - true_negatives: 1579.0000 - false_positives: 3531.0000 - false_negatives: 1579.0000
Epoch 5/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.7236 - true_positives: 3528.0000 - true_negatives: 1595.0000 - false_positives: 3515.00

Epoch 42/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6986 - true_positives: 3260.0000 - true_negatives: 2018.0000 - false_positives: 3092.0000 - false_negatives: 1860.0000
Epoch 43/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6981 - true_positives: 3259.0000 - true_negatives: 2031.0000 - false_positives: 3079.0000 - false_negatives: 1861.0000
Epoch 44/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6976 - true_positives: 3266.0000 - true_negatives: 2035.0000 - false_positives: 3075.0000 - false_negatives: 1854.0000
Epoch 45/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6972 - true_positives: 3262.0000 - true_negatives: 2042.0000 - false_positives: 3068.0000 - false_negatives: 1858.0000
Epoch 46/20000
1023/1023 [==============================] - 0s 7us/sample - loss: 0.6967 - true_positives: 3262.0000 - true_negatives: 2047.0000 - false_positives: 3063.0000 - false_negati

Epoch 83/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6828 - true_positives: 3420.0000 - true_negatives: 2478.0000 - false_positives: 2632.0000 - false_negatives: 1700.0000
Epoch 84/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6825 - true_positives: 3428.0000 - true_negatives: 2492.0000 - false_positives: 2618.0000 - false_negatives: 1692.0000
Epoch 85/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6822 - true_positives: 3435.0000 - true_negatives: 2508.0000 - false_positives: 2602.0000 - false_negatives: 1685.0000
Epoch 86/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6818 - true_positives: 3441.0000 - true_negatives: 2533.0000 - false_positives: 2577.0000 - false_negatives: 1679.0000
Epoch 87/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6815 - true_positives: 3454.0000 - true_negatives: 2536.0000 - false_positives: 2574.0000 - false_negati

Epoch 124/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6709 - true_positives: 3430.0000 - true_negatives: 3040.0000 - false_positives: 2070.0000 - false_negatives: 1690.0000
Epoch 125/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6707 - true_positives: 3426.0000 - true_negatives: 3065.0000 - false_positives: 2045.0000 - false_negatives: 1694.0000
Epoch 126/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6704 - true_positives: 3435.0000 - true_negatives: 3078.0000 - false_positives: 2032.0000 - false_negatives: 1685.0000
Epoch 127/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6701 - true_positives: 3430.0000 - true_negatives: 3089.0000 - false_positives: 2021.0000 - false_negatives: 1690.0000
Epoch 128/20000
1023/1023 [==============================] - 0s 6us/sample - loss: 0.6699 - true_positives: 3437.0000 - true_negatives: 3098.0000 - false_positives: 2012.0000 - false_n

Epoch 165/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6602 - true_positives: 3559.0000 - true_negatives: 3426.0000 - false_positives: 1684.0000 - false_negatives: 1561.0000
Epoch 166/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6599 - true_positives: 3580.0000 - true_negatives: 3421.0000 - false_positives: 1689.0000 - false_negatives: 1540.0000
Epoch 167/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6596 - true_positives: 3577.0000 - true_negatives: 3444.0000 - false_positives: 1666.0000 - false_negatives: 1543.0000
Epoch 168/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6594 - true_positives: 3595.0000 - true_negatives: 3434.0000 - false_positives: 1676.0000 - false_negatives: 1525.0000
Epoch 169/20000
1023/1023 [==============================] - 0s 5us/sample - loss: 0.6591 - true_positives: 3589.0000 - true_negatives: 3455.0000 - false_positives: 1655.0000 - false_n

...

Epoch 19823/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19824/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19825/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19826/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19827/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0

Epoch 19863/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19864/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19865/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19866/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19867/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0041 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0

Epoch 19903/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19904/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19905/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19906/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19907/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0

Epoch 19943/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19944/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19945/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19946/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19947/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0

Epoch 19983/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19984/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19985/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19986/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0.0000e+00 - false_negatives: 0.0000e+00
Epoch 19987/20000
1023/1023 [==============================] - 0s 4us/sample - loss: 0.0040 - true_positives: 5120.0000 - true_negatives: 5110.0000 - false_positives: 0

### $\textbf{Get Activations of Hidden & Output Layers}$

In [9]:
######################################
# Hidden sigmoidal layer activations #
######################################

# Gather hidden layer outputs from original model
h_layer = model.get_layer('hidden').output

# Separate model to spy on hidden layer activations
hidden_layer_model = Model(inputs=model.input,
    outputs=h_layer)

# Sigmoidal hidden layer outputs / activations
hidden_activations = hidden_layer_model.predict(X)

######################################
# Output sigmoidal layer activations #
######################################

# Get model output activations
output_activations = model.predict(X)

### $\textbf{Plot LFSR State Observation & Network's Future State Predictions}$

In [10]:
# Plot true n'th vs. predicted (n + 1)'st'...
if plot_prediction_masks:
    
    # Plot LFSR state progression & predicted progression (in parallel)
    true_vs_predicted_masks(idx0=0, idx1=50, input_obs=X,
                            output_activations=output_activations)

<IPython.core.display.Javascript object>

### $\textbf{Visualize Convergence of Metrics vs. Training Epoch}$

In [11]:
# Metrics plot enabled?...
if plot_metrics_versus_epoch:
    
    # Plot {TP,TN,FP,FN} vs. training epoch
    plot_metrics_vs_epoch(model, N_epoch)

TypeError: plot_metrics_vs_epoch() missing 1 required positional argument: 'N_epoch'

### $\textbf{Visualize LFSR State and Feedforward Binary Network}$

In [ ]:
##############################
# Visualization config panel #
##############################

config = {
    'figsize': (9.9, 7),
    'deg': deg,
    'x_mid': (deg - 1) / 2,
    'cmap': 'cividis',
    'y_input': 0,
    'y_hidden': 0.45,
    'y_output': 0.9,
    'y_decision': 1,
    'y_LFSR_loop': -0.1,
    'ylim': [-0.32, 1.2],
    'num_hidden': deg + 2,
    'num_input': deg,
    'num_output': deg,
    'node_size': 10,
    'link_width': 1,
    'net_link_alpha': 0.6,
    'arrow_size': 8,
    'net_feedback_linestyle':'--'
}

lfsr_prediction_animation(
    lfsr=LFSRs[p], config=config, model=model,
    state_sequence=X, hidden_activations=hidden_activations,
    output_activations=output_activations,
    run_animation=True, interval=1000, blit=True, repeat=True)

In [ ]:
type(model_history)